In [ ]:
import pandas as pd

df = pd.read_csv("../previsions/PETR4_D1_high.csv")
df.columns = ["time", "high"]
df_low = pd.read_csv("../previsions/PETR4_D1_low.csv")
df_low.columns = ["time", "low"]
df["low"] = df_low["low"]


In [24]:
from trader import Trader
import pandas as pd
from datetime import date
import matplotlib.pyplot as plt


trader = Trader(0.33, 0.66)
df = pd.read_csv("C:\\Users\\gustavo.barros\\Documents\\UFMG\\TCC\\previsions\\WDO@N_D1_high.csv")
df.columns = ["time", "high"]
df_low = pd.read_csv("C:\\Users\\gustavo.barros\\Documents\\UFMG\\TCC\\previsions\\WDO@N_D1_low.csv")
df_low.columns = ["time", "low"]
df["low"] = df_low["low"]
df['date'] = pd.to_datetime(df['time'],unit='s').dt.date
# df = df[df['date'] > date(2021,8,29)]

df_close = pd.read_csv("C:\\Users\\gustavo.barros\\Documents\\UFMG\\TCC\\data\\WDO@N_M15_close.csv")
df_close.columns = ["time", "close"]
df_close['time'] = pd.to_datetime(df_close['time'],unit='s')

orders = []
for index, row in df_close.iterrows():
    today = df[df["date"] == row["time"].date()]
    if not len(today["low"]): continue
    # print(today)
    try:
        is_last_candle_day = df_close.iloc[index]["time"].date() != df_close.iloc[index + 1]["time"].date()
    except:
        is_last_candle_day = True

    trader.min_ann = today["low"].item()
    trader.max_ann = today["high"].item()

    order, order_nature = trader.send_order(row["close"], 
        is_last_candle_day
    )

    orders.append({
        "order": order, 
        "order_nature": order_nature, 
        "min_ann": today["low"].item(),
        "max_ann": today["high"].item(), 
        "time": row["time"],
        "close": row["close"]
    })

df_orders = pd.DataFrame(orders)


# Assuming that dataframes df1 and df2 are already defined:


In [25]:
from IPython.display import display, HTML

df_orders_without_zeros = df_orders[df_orders["order"] != 0].reset_index(drop=True)
df_orders_exit_order = df_orders_without_zeros[(df_orders_without_zeros.index % 2) == 0].reset_index(drop=True)
df_orders_exit_order[["exit_order", "exit_price", "exit_order_nature"]] = df_orders_without_zeros[(df_orders_without_zeros.index % 2) == 1].reset_index(drop=True).reset_index(drop=True)[["time", "order", "order_nature"]]
df_orders_exit_order["result"] = -(df_orders_exit_order["order"] + df_orders_exit_order["exit_price"])


In [30]:
# df_orders
import plotly.express as px
import plotly.graph_objects as go


fig = px.line(df_orders, x="time", y=["min_ann", "max_ann", "close"])
fig.add_trace(go.Scatter(x=df_orders["time"], y=abs(df_orders["order"]),
    mode='markers',
    name='markers',
    marker=dict(
        size=10,
        # I want the color to be green if 
        # lower_limit ≤ y ≤ upper_limit
        # else red
        color=(
            (df_orders["order"] > 0)
        ).astype('int'),
        colorscale=[[0, 'red'], [1, 'green']]
    )
))
# fig = fig.addscatter(df_orders, x="time", y="order")
fig.show()

# sns.show()

# df_orders['order'].plot(secondary_y=True, kind="bar")

In [31]:
fig = px.scatter(df_orders, x="time", y="order")
fig.show()

In [32]:
df_orders_exit_order["cum_result"] = df_orders_exit_order["result"].cumsum()

fig = px.line(df_orders_exit_order, x="time", y=["min_ann", "max_ann", "close", "cum_result"])
fig.show()

In [29]:
display(HTML(df_orders_exit_order.to_html()))